In [ ]:
# Tests of ipywidgets
import ipywidgets as widgets

from IPython.display import display
# Simple slider (Integer)
w = widgets.IntSlider()
w.min = 10 ; w.max = 20
display(w)

In [ ]:
print("Value from Slider",w.value)

In [ ]:
# Linking widgets (format does not seem yto do anything)
a = widgets.FloatText(readout_format='.1f')
b = widgets.FloatSlider(readout_format='.1f')
v = widgets.Valid(description='Above 50')
display(a,b,v)

mylink = widgets.jslink((a, 'value'), (b, 'value'))
print("Change Value and then execute cell below")

In [4]:
# Test value and change Valid widget is > 50 
# 
# a.value
if a.value > 50 :
    v.value = True
    

In [ ]:
# Enter a string and see what text was entered in next cell
wt = widgets.Textarea(
    value='xxxx',
    placeholder='Type something',
    description='Station Code:',
    disabled=False
)
display(wt)


In [ ]:
print('String from Textarea:',wt.value)
print('Value from first slider at top of NoteBook',w.value)

In [ ]:
# Make selectio from group
wc = widgets.Combobox(
    # value='John',
    placeholder='Choose Someone',
    options=['Paul', 'John', 'George', 'Ringo'],
    description='Combobox:',
    ensure_option=True,
    disabled=False
)
display(wc)

In [ ]:
print('Choice from combobx:',wc.value)

In [ ]:
play = widgets.Play(
    value=50,
    min=0,
    max=100,
    step=1,
    interval=500,
    description="Press play",
    disabled=False
)
slider = widgets.IntSlider()
widgets.jslink((play, 'value'), (slider, 'value'))
widgets.HBox([play, slider])

In [ ]:
# Date and Time selector
wD = widgets.DatetimePicker(
    description='Pick a Time',
    disabled=False
)
display(wD)

In [ ]:
print('All outputs from widgets')
print('Date and Time:',wD.value)
print("Value from Slider",w.value)
print('Linked slider',a.value, b.value)
print('String from Textarea:',wt.value)
print('Choice from combobx:',wc.value)
print('Animated Slider',slider.value)



**Interactive Exemple for ipywidget plot creation**
<br>
Test case below (maybe be useful for PSET02.) You can chaneg the equation to make different plots.  There are still some issues with interactive plots but you can play witj that


In [ ]:
# Text Box that show how to have input text and have a plot
# generated.
# Tests of ipywidgets
import ipywidgets as widgets
from IPython.display import display
from ipywidgets import HBox, VBox

import numpy as np
import matplotlib.pyplot as plt
from math import *
import sys
import matplotlib as mpl



# Function to read expression and range and make plot
def MakePlot(x) :
    # See if interactive figure 
    if wpmpl.value :
        # Turn on interactive, check OS
        systype = sys.platform
        if (systype=='darwin' ) :
            mpl.use('macosx'); 
            %matplotlib
        else:
            mpl.use('qt5agg'); 
            %matplotlib
    else :       
        %matplotlib inline

    print('Using backend ',mpl.get_backend())

    # Function to make plot
    expr = wpt.value   # Equation in box
    lb = wpl.value ; ub = wpu.value   # Upper and lower bounds
    tr = np.arange(lb,ub,(ub-lb)/100)
    ydata = np.empty(shape=0)
    for t in tr :
        ydata = np.append(ydata,eval(expr))
        

    if wpc.value :
       fig = plt.figure;
       fig(figsize=(8,4))
       wpc.value = False
    
    plt.plot(tr,ydata)
    plt.title(expr)
    plt.xlabel("t")
    plt.ylabel("ydata")
    plt.draw()



# Create widgets for expression entry and range
wpt = widgets.Textarea(
    value='sin(2*pi*t)',
    placeholder='Enter Expressoion',
    description='Expression',
    disabled=False
)
wpl = widgets.FloatText(description='Lower',value=0)

wpu = widgets.FloatText(description='Upper',value=2*pi)

wpr = widgets.Button(description="Plot", icon = "line-chart")
wpr.style.button_color = 'paleturquoise'

wpc = widgets.Checkbox(value=True,description='New Plot')
wpmpl = widgets.Checkbox(value=False,description='Matplotlib')



wpr.on_click(MakePlot)



WidgetPlot_window = VBox([
    widgets.HTML('<h1>Equation entry</h1>'),
    HBox([wpt,wpc,wpmpl]),
    HBox([wpl,wpu,wpr])
 ])

display(WidgetPlot_window)


In [ ]:
# Seems to be needed to get interactive graphic to appear
%matplotlib 

**Earthscope/Unavco Data access**
<br>
The two cells below show how set up access to the Earthscope data portal. Onces the cells have been execuated, try the third cell to download file.  
You can change the directory paths to set your needs (files downloaded into current directory but yoiu could creat as "data" sub-directory and
then use ./data)

In [ ]:
# See if we need to install earthscope_sdk
try:
    from earthscope_sdk.auth.device_code_flow import DeviceCodeFlowSimple
    from earthscope_sdk.auth.auth_flow import NoTokensError
    print('earthscope_sdk aleady installed in virtual environment')
except:
    # Install earthscope_sdk
    print('Installing earthscope_sdk in virtual environment')
    %pip install earthscope_sdk

In [15]:
import requests
from pathlib import Path
 
from earthscope_sdk.auth.device_code_flow import DeviceCodeFlowSimple
from earthscope_sdk.auth.auth_flow import NoTokensError

def get_es_file(url, directory_to_save_file='./', token_path='./'):
    """function to get earthscope data using es-sdk

    Parameters
    ----------
    url : string
        url of desired file at gage-data.earthscope.org
    directory_to_save_file : str, optional
        path of directory in which to save the file, by default cwd
    token_path : str, optional
        path of directory in which to save the token, by default './'
    """
    # instantiate the device code flow subclass
    device_flow = DeviceCodeFlowSimple(Path(token_path))
    try:
      # get access token from local path
      device_flow.get_access_token_refresh_if_necessary()
    except NoTokensError:
      # if no token was found locally, do the device code flow
      device_flow.do_flow()
    token = device_flow.access_token

    # request a file and provide the token in the Authorization header
    file_name = Path(url).name

    r = requests.get(url, headers={"authorization": f"Bearer {token}"})
    if r.status_code == requests.codes.ok:
      # save the file
      with open(Path(Path(directory_to_save_file) / file_name), 'wb') as f:
        for data in r:
            f.write(data)
    else:
      #problem occured
      print(f"failure: {r.status_code}, {r.reason}")

In [16]:
# Test trying to get this file.  The first time you are likely to see a message like:
#To complete the SSO authorization, please visit the following URL in a browser of your choice:
#            https://login.earthscope.org/activate?user_code=????-????
#
get_es_file("https://data.unavco.org/archive/gnss/products/position/P179/P179.cwu.nam14.csv")